In [60]:

import yfinance as yf
import pandas as pd
import plotly.graph_objects as go
from datetime import datetime


symbol = "BTC-USD"
start_date = "2023-01-01"
end_date = datetime.now().strftime('%Y-%m-%d')  # Today's date in 'YYYY-MM-DD' format
interval = "1h"
data = yf.download(symbol, start=start_date, end=end_date, interval=interval)
data.to_csv('BTCUSD_Hourly_01.01.2023-Today.csv')

[*********************100%%**********************]  1 of 1 completed


In [61]:
# Cell 3: Data Preparation
data.index = pd.to_datetime(data.index)  # Ensure the index is in datetime format
data.dropna(inplace=True)  # Clean data by removing NaN rows

# Cell 4: Indicator Calculations

# Calculate Exponential Moving Average for MACD
exp1 = data['Close'].ewm(span=12, adjust=False).mean()
exp2 = data['Close'].ewm(span=26, adjust=False).mean()
data['MACD'] = exp1 - exp2
data['MACDs'] = data['MACD'].ewm(span=9, adjust=False).mean()

# Calculate RSI
delta = data['Close'].diff()
gain = (delta.where(delta > 0, 0)).ewm(span=14, adjust=False).mean()
loss = (-delta.where(delta < 0, 0)).ewm(span=14, adjust=False).mean()
rs = gain / loss
data['RSI'] = 100 - (100 / (1 + rs))


In [68]:

def determine_signal(row):
    if row['RSI'] > 70 and row['MACD'] < row['MACDs']:
        return -1  # Sell
    elif row['RSI'] < 30 and row['MACD'] > row['MACDs']:
        return 1   # Buy
    return 0

data['Signal'] = data.apply(determine_signal, axis=1)

print("Buy signals count:", data[data['Signal'] == 1].shape[0])
print("Sell signals count:", data[data['Signal'] == -1].shape[0])


Buy signals count: 48
Sell signals count: 81


In [63]:

# Cell 6: Visualization with Buy and Sell Markers
fig = go.Figure(data=[
    go.Candlestick(x=data.index,
                   open=data['Open'], high=data['High'],
                   low=data['Low'], close=data['Close']),
    go.Scatter(x=data.index, y=data['RSI'], name='RSI',
               line=dict(color='blue', width=2)),
    go.Scatter(x=data.index, y=data['MACD'], name='MACD',
               line=dict(color='red', width=2)),
    go.Scatter(x=data.index, y=data['MACDs'], name='Signal line',
               line=dict(color='green', width=2)),
    go.Scatter(x=data.index[data['Signal'] == 1], y=data['Low'][data['Signal'] == 1] * 0.99, 
               mode='markers', name='Buy Signal', marker=dict(symbol='triangle-up', size=10, color='blue')),
    go.Scatter(x=data.index[data['Signal'] == -1], y=data['High'][data['Signal'] == -1] * 1.01, 
               mode='markers', name='Sell Signal', marker=dict(symbol='triangle-down', size=10, color='yellow'))
])

fig.update_layout(title='BTC Trading Signals', xaxis_title='Date', yaxis_title='Price')
fig.show()

In [70]:
# Cell 7: Trading Strategy Results Summary
def simulate_trades(data):
    initial_capital = 1000.0
    capital = initial_capital
    unit = 1
    positions = 0
    trade_results = []

    for index, row in data.iterrows():
        if row['Signal'] == 1:  # Buy signal
            if capital >= row['Close'] * unit:
                capital -= row['Close'] * unit
                positions += unit
                trade_results.append({'Date': index, 'Type': 'Buy', 'Price': row['Close'], 'Units': unit, 'Capital': capital})
        elif row['Signal'] == -1:  # Sell signal
            if positions >= unit:
                capital += row['Close'] * unit
                positions -= unit
                trade_results.append({'Date': index, 'Type': 'Sell', 'Price': row['Close'], 'Units': unit, 'Capital': capital})

    final_value = capital + positions * data.iloc[-1]['Close']
    profit = final_value - initial_capital
    results_df = pd.DataFrame(trade_results)

    return results_df, final_value, profit

# Simulate the trades and output the results
trade_results_df, final_value, profit = simulate_trades(data)
print("Trade Transactions:")
print(trade_results_df)
print("\nFinal Capital: ${:.2f}".format(final_value))
print("Profit: ${:.2f}".format(profit))


Trade Transactions:
Empty DataFrame
Columns: []
Index: []

Final Capital: $1000.00
Profit: $0.00
